In [1]:
import random
import numpy as np
import math
import torch
import torch.nn as nn
import torch.nn.functional as F
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.animation
from game_world import GameWorld

In [2]:
class Policy(nn.Module):

    def __init__(self, action_size):
        super().__init__()
        self.layer1 = nn.Linear(5, 64)
        self.layer2 = nn.Linear(64, 32)
        self.layer3 = nn.Linear(32, 32)
        self.layer4 = nn.Linear(32, action_size)

    def forward(self, input: torch.tensor) -> int:
        x = F.relu(self.layer1(input))
        x = F.relu(self.layer2(x))
        x = F.relu(self.layer3(x))
        x = self.layer4(x)
        x = torch.argmax(x, dim=1)
        return x[0]

class Agent:
    """
    the REINFORCE agent

    args:
        policy_path: the policy module weight path
    """
    def __init__(self, policy_path):
        self.action_size = 2

        self.device = torch.device('cpu')
        self.pi = Policy(self.action_size)
        self.pi.load_state_dict(torch.load(policy_path, map_location=self.device, weights_only=True))
        self.pi.to(self.device)
        self.pi.eval()

    def get_action(self, state) -> int:
        state = torch.tensor([state], device=self.device, dtype=torch.float32)
        action = self.pi(state)
        return action.item()


In [3]:
AREA_WIDTH = 1200
AREA_HEIGHT = 600
PADDLE_HEIGHT = 50

agent = Agent("./reinforce_model_params.pth")

In [6]:
# the game world
env = GameWorld(AREA_WIDTH, AREA_HEIGHT)
start_state = env.reset()

trajectory = []
trajectory.append(start_state)

actions = []
paddle_positions = []
state = start_state

while True:
    action = agent.get_action(state)
    actions.append(action)
    
    next_state, reward, done, hit = env.step(action=action, step_num=3)
    trajectory.append(next_state)
    
    paddle_positions.append(next_state[4] * AREA_HEIGHT)
    state = next_state
    if done:
        break
env.destroy_bodies()

print(f"the ball start at: ({start_state[0] * AREA_WIDTH}, {start_state[1] * AREA_HEIGHT}), velocity: ({start_state[2] * AREA_WIDTH}, {start_state[3] * AREA_HEIGHT})")
print(f"the trajectory length: {len(trajectory)}")
print(f"the final state reward: {reward}")
print(f"the paddle final pos: {paddle_positions[-1]}")
print(f"hit: {hit}")

the ball start at: (10.0, 306.1603088378906), velocity: (81.32969665527344, -81.80127716064453)
the trajectory length: 292
the final state reward: 4.208824972228197
the paddle final pos: 305.3664245605469
hit: True


In [7]:
paddle_height = 50
paddle_x = env.paddle_x

plt.xlim(0, AREA_WIDTH+20)
plt.ylim(0, AREA_HEIGHT+20)

x = [item[0]*AREA_WIDTH for item in trajectory]
y = [item[1]*AREA_HEIGHT for item in trajectory]

#render the start point
plt.scatter(x[0], y[0], color='red', s=40)
#render the end point
plt.scatter(x[len(trajectory)-1], y[len(trajectory)-1], color='blue', s=40)
#render the trajectory
plt.plot(x, y, linewidth=2)
plt.show()

#animate the ball trajectory
fig, ax = plt.subplots()
plt.xlim(0, AREA_WIDTH+20)
plt.ylim(0, AREA_HEIGHT+20)

paddle_pos, = ax.plot([paddle_x, paddle_x], [trajectory[0][4]*AREA_HEIGHT-paddle_height/2, trajectory[0][4]*AREA_HEIGHT+paddle_height/2], linewidth=2, color='black')
ball_pos = ax.scatter(trajectory[0][0]*AREA_WIDTH, trajectory[0][1]*AREA_HEIGHT, color='blue', s=20)

def animate(i):
    ball_pos.set_offsets([x[i], y[i]])
    paddle_pos.set_data([paddle_x, paddle_x], [trajectory[i][4]*AREA_HEIGHT-paddle_height/2, trajectory[i][4]*AREA_HEIGHT+paddle_height/2])

ani = matplotlib.animation.FuncAnimation(fig, animate, frames=len(trajectory), interval=10)

plt.close()

from IPython.display import HTML
#very slow
HTML(ani.to_jshtml())